Skript zum Kurs
# Computergestützte Datenauswertung
im Bachelorstudiengang Physik am Karlsruher Institut für Technologie (KIT)

U. Husemann (basierend auf Materialien von G. Quast, T. Ferber und U. Husemann)

Sommersemester 2024

# Kapitel 4: Statistische Datenanalyse II – Parameterschätzung (Teil 1)
Die **Parameterschätzung** ist ein Teilgebiet der mathematischen Statistik und ein wichtiges Werkzeug in der Physik. Aufgabe und Ziel der Parameterschätzung ist es, aus einer potenziell sehr großen Datenmenge eine (hoffentlich kleine) Anzahl von Modellparametern zu schätzen. Dabei verstehen wir den Begriff "Schätzung" im Sinne eines systematischen Verfahrens zur Bestimmung eines (in gewissem Sinne optimalen) Wertes und einer Unsicherheit für die Modellparameter. In der Sprache der Statistik schließen wir dabei aus einer Stichprobe auf die Eigenschaften einer Wahrscheinlichkeitsverteilung, beispielsweise deren Erwartungswert und Standardabweichung. Als Schätzwerte verwenden wir dazu arithmetisches Mittel und Standardunsicherheit der Stichprobe. 

>**Beispiel: Lebensdauer kosmischer Myonen** In einem Versuch soll die Lebensdauer von Myonen aus der kosmischen Strahlung bestimmt werden. Myonen sind Geschwisterteilchen der Elektronen, besitzen aber eine 200-fach größere Masse und sind nicht stabil, sondern zerfallen in rund 2,2 Mikrosekunden. Ihre Lebensdauer kann bestimmt werden, indem sie in Materie gestoppt werden und dann die Zeitspanne zwischen Einfang und Zerfall bestimmt wird. Das physikalische Modell dazu ist ein exponentieller Zerfall mit der PDF $f(t;\tau)=1/\tau\exp[-t/\tau]$, wobei der Skalierungsparameter $\tau$ der mittleren Lebensdauer entspricht. Im folgenden Codebeispiel (das in Kapitel 2 schon so ähnlich zur Illustration von Unsicherheitsbalken verwendet wurde) wird das simuliert und dann die mittlere Lebensdauer und deren Unsicherheit geschätzt.

In [ ]:
"""model muon lifetime and its estimate"""
import numpy as np
import matplotlib.pyplot as plt

rng = np.random.default_rng()
n = 100
tau_true = 2.2e-6
data = rng.exponential( scale=tau_true, size=n )

fig,ax = plt.subplots()

# lines at the random data
ax.vlines( data, 0, 1, linestyles='-', lw=2)

# box-whisker plot to illustrate distribution
boxy = 2.
ax.boxplot( data, positions=[boxy], vert=False , notch=False )

# estimate tau and its uncertainty
meanx = np.mean( data )
meany = 3.
stdx  = np.std( data, ddof=1 )/np.sqrt( len(data) )
ax.errorbar( meanx, meany, xerr=stdx, fmt='-ro' )
ax.text( 1.2*meanx, meany-0.05, r"$\hat\tau = %4.2f \pm %4.2f\, \mathsf{\mu s}$" % ( 1e6*meanx, 1e6*stdx ) )


ax.set_ylim( 0, 4 )
ax.set_yticks ( [] )
ax.ticklabel_format( style='sci', scilimits=(-6,-6), axis='x' )
ax.set_xlabel( "$t (s)$") 

plt.show()

Eine weitere typische Aufgabe der Parameterschätzung ist die **Anpassung einer Modellfunktion** an Daten, um deren freie Parameter und deren Unsicherheit zu schätzen. Dies wird im Jargon auch gern als "Fit" bezeichnet. Wenn das Modell ein physikalisches Modell ist, also z. B. einen Teilaspekt eines physikalischen Gesetzes abbildet, können die entsprechenden physikalischen Parameter direkt durch die Anpassung geschätzt werden. Das einfachste Beispiel dafür ist die "Ausgleichsgerade", bei der das Modell aus der Funktionsvorschrift für eine lineare Funktion $y=f(x)=mx+c$ mit der Steigung $m$ und dem $y$-Achsenabschnitt $c$ als freue Parameter ist. Der fachsprachliche Ausdruck für diese Klasse von Anpassungsaufgaben lautet "**lineare Regression**". Dabei bezieht sich "linear" auf Linearität in den Parametern (hier: $m$ und $c$), während die unabhängigen Variablen (hier: $x$) nicht notwendigerweise linear in die Modellfunktion eingehen müssen.

>**Beispiel: Ausgleichsgerade**
>
> Eine Strom-Spannungskennlinie eines elektrischen Widerstands wird aufgenommen. Dazu werden an den Widerstand feste, als exakt bekannt angenommene, elektrische Spannungen $U$ angelegt und der Strom $I(U)$ gemessen. Als einzige Unsicherheit der einzelnen Strommessungen wird die Ablesegenauigkeit der Skala des Messgeräts als statistische Unsicherheit berücksichtigt. Beide Annahmen sind Vereinfachungen, die im physikalischen Praktikum häufig verwendet werden, aber nicht immer gerechtfertigt sind. An die Datenpunkte wird die Modellfunktion $I(U) = 1/R\cdot U$ per linearer Regression angepasst. Der Parameter dieses physikalischen Modells ist die Steigung $1/R$, der Kehrwert des Widerstandes $R$, auch elektrischer Leitwert $G$ genannt. Aus Schätzwert und Unsicherheit von $G$, also $\hat G\pm \sigma_{\hat G}$, wird dann durch Fortpflanzung der Unsicherheit ($G$ und $1/G$ besitzen dieselbe relative Unsicherheit) die Unsicherheit auf $R=1/G$ berücksichtigt, um zum Ergebnis $\hat R \pm \sigma_{\hat R}$ zu gelangen. Eine Anpassung direkt mit $R$ als Modellparameter ist mit heutiger Software auch problemlos möglich, diese Modellfunktion ist dann aber nicht mehr linear im Modellparameter, und somit handelt es sich nicht um eine lineare Regression. Das folgende Codebeispiel simuliert die Strom-Spannungs-Kennlinie mit Zufallszahlen und verwendet (im Vorgriff auf weitere Abschnitte in diesem Kapitel) eine SciPy-Routine für die lineare Regression. Der Leitwert ist im Rahmen seiner Unsicherheiten mit dem wahren Wert 0.001 Siemens verträglich.

In [ ]:
"""Using SciPy.optimize.curve_fit for a straight-line fit to Ohm's law"""
import numpy as np
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit

def current_ohm_model( V, G=1. ):
	'''Ohm's law'''
	return G*V

# generate N data points
N = 11

# minimum/maximum voltage in volts
Vmin, Vmax = 1, 10

# resistance in ohm, conductance in siemens
R = 1000
G = 1/R

# current uncertainty in A (from limited resolution of ammeter)
sigmaI = np.ones(N)*5e-4

rng = np.random.default_rng( 42 )

# generate data points according to Ohm's law shifted by random offset
V = np.linspace( Vmin, Vmax, N )
I = current_ohm_model( V, G ) + rng.normal( size=N, scale=sigmaI )

# plot data points
fig,ax = plt.subplots()
plt.errorbar( V, I, sigmaI,fmt='bo') 
plt.xlabel('$V$ (V)')
plt.ylabel('$I$ (A)')

# fit with curve_fit (uncertainty only correct when explicitly switching on absolute uncertainites)
popt, pcov = curve_fit( current_ohm_model, V, I, sigma=sigmaI, absolute_sigma=True )

# plot fitted curve
Vrange = np.linspace( Vmin-0.5, Vmax+0.5, 200 )
ax.plot( Vrange, current_ohm_model( Vrange, *popt), 'r-' )

# print fit parameters
ax.text( Vmin, 0.010, r"$G$ = %5.3f $\pm$ %5.3f mS" % ( 1e3*popt[0], 1e3*np.sqrt(pcov[0][0]) ) )

plt.show()

Allgemein gesprochen beantwortet die Parameterschätzung die Frage, für welche Wahl der Modellparameter eine gegebene **Modellfunktion am besten zu den Daten passt**. Dafür gibt es in der Literatur mehrere Ansätze:
- Im Rahmen dieses Kurses werden wir die **Methode der kleinsten Quadrate** (auch $\chi^2$-Methode, engl.: least squares method, LS) behandeln, die Anfang des 19. Jahrhunderts von Carl Friedrich Gauß, Pierre-Simon Laplace und Adrien-Marie Legendre entwickelt wurde. Die lineare Regression für Anpassungen, z. B. für die Ausgleichsgerade im physikalischen Praktikum (siehe obiges Codebeispiel), ist ein Beispiel für diese Methode. Eine weitere Beschreibung der LS-Methode und ihrer praktischen Anwendung ist im Skript [Funktionsanpassung mit der $\chi^2$-Methode](https://etpwww.etp.kit.edu/~quast/Skripte/Chi2Method.pdf) von Günter Quast zu finden.
- Später in Ihrem Studium werden Sie mit der von Ronald Aylmer Fischer entwickelten **Maximum-Likelihood-Methode** (ML) ein moderneres Verfahren kennenlernen. Es ist universell einsetzbar zur systematischen Konstruktion von Schätzern mit "optimalen" Eigenschaften. Dazu gehören eine unverzerrte ("erwartungstreue") Schätzung des wahren Werts sowie eine möglichst kleine Varianz. Ein erster Einstieg in ML-Methoden findet sich am Ende dieses Kapitels im Ausblick.

## Methode der kleinsten Quadrate
Die Methode der kleinsten Quadrate beruht darauf, den Abstand zwischen einem Modell und Daten an $n$  Positionen $x_i$ zu minimieren. Die Modellparameter werden so optimiert, dass der *gesamte* Abstand möglichst gering ist. Als Abstandsmaß für einen Datenpunkt $y_i$ mit einer an einer Position $x_i$ von der Modellerwartung $\lambda_i$ mit Varianz $\sigma_i^2$ wird das Residuenquadrat verwendet, d. h. der quadratische Abstand normiert auf die Varianz:
$$
d_i^2\equiv\frac{(y_i-\lambda_i)^2}{\sigma_i^2}.
$$ 
Als Gesamtabstand wird dann die Summe der Residuenquadrate $S$, in der Literatur auch als $\chi^2$ bezeichnet, verwendet:
$$
S \equiv \chi^2 \equiv \sum_{i=1}^n d_i^2 \equiv \sum_{i=1}^n\frac{(y_i-\lambda_i)^2}{\sigma_i^2}.
$$

Für eine Ausgleichsgerade finden sich diese Größen in folgender Skizze:

<img src="img/straight_line_fit.png" width=50%>

>**Bemerkung: $S$ oder $\chi^2$?** In Kapitel 2 wurde bereits der Zusammenhang zwischen der Summe der Residuenquadrate und der $\chi^2$-Verteilung erläutert: für normalverteilte Messwerte $y_i$ folgt $S$ einer $\chi^2$-Verteilung. In der Literatur wird die Funktion $S$ deswegen häufig einfach selbst als $\chi^2$ bezeichnet, und die Methode der kleinsten Quadrate heißt auch **$\chi^2$-Methode**. Zur besseren Unterscheidung von $S$ und der $\chi^2$-Verteilung wird hier und im weiteren das Symbol $S$ für die Summe der Residuenquadrate verwendet.

Für die verwendeten Größen ist zu beachten:
- $x_i$ ($i=1,\dots,n$) ist die $i$-te Position und wird als **exakt bekannt** angenommen. Für Messdaten ist das nicht immer eine gute Annahme, denn sie beinhalten in der Regel auch Unsicherheiten in $x_i$. Solche Unsicherheiten sind aber mit einer Standard-LS-Anpassung (und mit Standardwerkzeugen) nicht einfach behandelbar. Dieser Punkt wird im Abschnitt über Funktionsanpassung in der Praxis noch einmal aufgegriffen.
- $y_i$ ist der Messwert bzw. Datenpunkt an Position $x_i$.
- $\lambda_i$ ist der wahre Wert der Modellfunktion an Position $x_i$. Die Modellfunktion enthält $m$ Parameter $\mathbf{a}=(a_1,\dots,a_m)^\mathsf{T}$, also $\lambda_i = \lambda_i(x_i;\mathbf{a})$, daher ist der wahre Wert von $\lambda_i$ **unbekannt**. Durch die Anpassung werden die optimal zu den Daten passenden Parameterwerte $\hat{\mathbf{a}}$ bestimmt. Die Methode der linearen LS erfordert, dass die Modellfunktion linear in $\mathbf{a}$ ist (aber nicht notwendigerweise linear in $x_i$).
- $\sigma_i^2$ ist die Varianz des wahren Werts $\lambda_i$ an der Position $x_i$. Sie wird als **bekannt** vorausgesetzt. In vielen Wissenschaftszweigen wird für eine lineare Regression $\sigma_i^2=1$ gesetzt. 
Dies deutet darauf hin, dass es kein brauchbares Modell der zugehörigen Unsicherheiten gibt. In der Physik dagegen sind solche Unsicherheitsmodelle bekannt oder die Unsicherheiten lassen sich über die Stichprobenvarianz aus den Daten schätzen. 
$$


>Mit der **Methode der kleinsten Quadrate** wird der Schätzwert $\hat{\mathbf{a}}$ für die Parameter einer Modellfunktion $\lambda_i(x_i;\mathbf{a})$ durch eine Minimierung der Summe der Residuenquadrate gewonnen:
>$$
S \equiv \chi^2\equiv \sum_{i=1}^{n} \frac{(y_i - \lambda_i(x_i;\mathbf{a}))^2}{\sigma_i^2}
\overset{!}{=}\mathsf{min}
>$$

An dieser Stelle einige weitere **Bemerkungen** zur Methode der kleinsten Quadrate:
- $S=S(\mathbf{a})$ ist eine **skalare** Funktion der **Parameter**. Sie wird ausgerechnet, indem die vorher bestimmten Datenpunkte $y_i$ und Varianzen $\sigma_i^2$ in den Ausdruck für $S$ eingesetzt werden, daher sind diese **keine** unabhängigen Variablen. Die Minimierung von $S$ ist demnach eine **Minimierung im Raum der Parameter**, nicht im Raum der Messwerte.
- Das oben beschriebenen Standardverfahren in der Physik ist in der statistischen Literatur unter dem Namen **gewichtete LS-Methode** (engl.: weighted least squares, WLS) bekannt. Die LS-Methode ohne Unsicherheiten wird in der Literatur als **gewöhnliche LS-Methode** (engl.: ordinary least squares, OLS) bezeichnet.  In der OLS-Methode wird folgende Größe minimiert:
$$
S_\mathsf{OLS} \equiv \sum_{i=1}^n(y_i-\lambda_i)^2\overset{!}{=}\mathsf{min}
$$
- Für korrelierte Messwerte $\mathbf{y}=(y_1,\dots,y_n)^T$ und bekannter Kovarianzmatrix $\mathbf{V}$ der Modellfunktion $\boldsymbol{\lambda}=(\lambda_1,\dots,\lambda_n)^T$ lässt sich die Methode der kleinsten Quadrate verallgemeinern, indem die Summe der Residuenquadrate durch den Mahalanobis-Abstand ersetzt wird. Dies wird in der statistischen Literatur als **verallgemeinerte LS-Methode** (engl.: generalized least squares, GLS) bezeichnet. In der GLS-Methode wird also folgender Ausdruck ("Mahalanobis-Abstand") minimiert:
$$
S_\mathsf{GLS} \equiv \chi^2 \equiv
(\mathbf{y} - \boldsymbol{\lambda}(\mathbf{x};\mathbf{a}))^\mathsf{T} \,
\mathbf{V}^{-1} \,
(\mathbf{y} - \boldsymbol{\lambda}(\mathbf{x};\mathbf{a}))
\overset{!}{=}\mathsf{min}
$$

### Minimierung der Summe der Residuenquadrate
Die Minimierung von $S(\mathbf{a})$ kann in einigen einfachen Fällen **analytisch** erfolgen. Die notwendige Bedingung für ein Minimum ist dann das Verschwinden *aller* partiellen Ableitungen nach den Parametern $a_i$:
$$
\frac{\partial S}{\partial a_i} \overset{!}{=} 0 \quad \textsf{für } i = 1, \dots, m.
$$
Dies lässt sich auch zusammenfassend als Gradient bezüglich $\mathbf{a}$ schreiben:
$$
\boldsymbol{\nabla}_\mathbf{a} S \equiv \textsf{grad}_\mathbf{a} S\overset{!}{=} 0.
$$
Im allgemeinen wird die Minimierung **numerisch** durchgeführt. Dazu gibt effiziente Algorithmen der **numerischen Optimierung** skalarer Funktionen in einem $m$-dimensionalen Parameterraum. Gerade durch den Boom des maschinellen Lernens im letzten Jahrzehnt sind auf diesem Feld neue, extrem leistungsfähige Algorithmen dazugekommen. In der Praxis, und wenn die Minimierung nicht zeitkritisch ist, werden auch einfache Fälle numerisch behandelt.

### Kleinste Quadrate analytisch 
#### Konstante Modellfunktion
Als Beispiel für die analytische Minimierung von $S$ wird hier der einfache Fall einer konstanten Modellfunktion $\lambda_i = a$ betrachtet. Diese Modellfunktion ist offensichtlich linear in $a$, es handelt sich also um eine lineare Regression. Die LS-Methode erfordert also die Minimierung von
$$
S = \sum_{i=1}^{n}\frac{(y_i-a)^2}{\sigma_i^2}. 
$$
Die Aufgabe $n$ Messwerte $y_i$ mit einer Konstante zu vergleichen und damit die insgesamt am besten "passende" Konstante zu finden entspricht der Suche nach einem Mittelwert für die $y_i$. Das Ergebnis der Rechnung sollte also ein LS-Schätzwert für den Mittelwert von Daten sein. Wir unterscheiden zwei Fälle:

**Fall 1: Gleiche Varianz** für jeden Messwert: $\sigma_i^2\equiv\sigma^2$. In diesem Fall wird der optimale Parameter $a$ bestimmt über
$$
\frac{\partial S}{\partial a} = 
\sum_{i=1}^{n} \frac{-2(y_i-a)}{\sigma^2} = 
-\frac{2}{\sigma^2}\left( \sum_{i=1}^{n} y_i - \sum_{i=1}^{n} a \right) =
-\frac{2}{\sigma^2}\left( \sum_{i=1}^{n} y_i - n\cdot a \right)
\overset{!}{=}0,
$$
wobei Konstanten vor die Summen gezogen wurden. Dieser Ausdruck ist Null, wenn der Ausdruck in Klammern Null ergibt, also
$$
\hat a = \frac{1}{n} \sum_{i=1}^{n} y_i,
$$
unabhängig von $\sigma^2$. Das ist das bekannte **arithmetische Mittel** der $y_i$. Die LS-Methode hat uns also "automatisch" das arithmetische Mittel der Messdaten als Schätzwert für den wahren Wert geliefert, um den die Messdaten streuen.

Diese Minimierung von $S$ als Funktion des Parameters $a$ hätte auch **numerisch** ausgeführt werden können. Wir können dies hier in einem Codebeispiel illustrieren, indem wir eine Reihe möglicher Werte von $a$ in obige Gleichung einsetzt und jeweils $S$ bestimmen ("Parameterscan"). Dann wird $S$ gegen $a$ aufgetragen, es entsteht eine Parabel. Ein numerischer Algorithmus würde dann das Minimum von $S(a)$ suchen. Wie wir später in diesem Kapitel sehen werden, hängt die Breite der Parabel mit der Unsicherheit auf die Schätzung von $a$.

In [ ]:
"""animated_leastSquares: illustration of least squares method"""
# U. Husemann, June 2021

# add this Jupyter magic command to enable animation on some systems (needs ipympl installed)
%matplotlib ipympl

import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as anim

# model
atrue = 3
sig   = 1

# data points
n = 10
xi = np.linspace( 1, n, n )

# scan possible values of parameter a
amin, amax, steps = 0., 6., 300
a = np.linspace( amin, amax, steps )

rng = np.random.default_rng( 42 )
yi = rng.normal( loc=atrue, scale=sig, size=n )

fig,ax = plt.subplots( 2, 1, figsize=(7,10) )
graph_data  = ax[0].errorbar( xi, yi, yerr=sig, fmt='ro')
graph_line, = ax[0].plot( [], [], 'b-', lw=2 )
graph_S,    = ax[1].plot( [], [], 'b-', lw=2 )
ax[0].set_xlabel( r"$x$")
ax[0].set_ylabel( r"$y$")
ax[0].set_ylim( amin, amax )
ax[1].set_xlabel( r"$a$")
ax[1].set_ylabel( r"$S$")
ax[1].set_xlim( amin, amax )
ax[1].set_ylim( 0, 100 )

def S( a, y, sig=1. ):
	return np.sum( ( ( y - a ) / sig )**2 )

def animate( step ):
	a_anim = a[:step+1]
	S_anim = [ S( a, yi, sig ) for a in a_anim ]
	graph_line.set_data( [0.5,10.5], [a_anim[-1],a_anim[-1]] )
	graph_S.set_data( a_anim, S_anim )
	return graph_line, graph_S

ani = anim.FuncAnimation( fig, animate, frames=steps, interval=30, repeat=False )
plt.show()

**Fall 2: Unterschiedliche Varianzen** für jeden Messwert: in diesem Fall ergibt die notwendige Bedingung für ein Minimum
$$
\frac{\partial S}{\partial a} = 
\sum_{i=1}^{n} \frac{-2(y_i-a)}{\sigma_i^2} = 
-2\left( \sum_{i=1}^{n} \frac{y_i}{\sigma_i^2} - a \sum_{i=1}^{n} \frac{1}{\sigma_i^2}\right)\overset{!}{=}0.
$$
Auch dieser Ausdruck ist Null, wenn der Ausdruck in Klammern Null ergibt. Mit dem Gewichtsfaktor $w_i = 1/\sigma_i^2$ lässt sich diese Bedingungen umschreiben zu:
$$
\sum_{i=1}^{n} w_i\cdot y_i \overset{!}{=} a \sum_{i=1}^{n} w_i
$$
und damit erhalten wir für den LS-Schätzwert für $a$:
$$
\hat a = \frac{1}{\sum_i w_i} \sum_{i=1}^{n} w_i\cdot y_i.
$$
Dies ist ebenfalls ein Mittelwert der Messdaten, mit dem Unterschied, dass jeder Messwert $y_i$ mit dem Gewichtsfaktor $w_i$ multipliziert wird, der seine "Wichtigkeit" für den Mittelwert bestimmt. Die Größe wird als **gewichteter Mittelwert** $\overline{x}$ (engl.: weighted mean) bezeichnet. Der Gewichtsfaktor ist der Kehrwert der Varianz, $w_i = 1/\sigma_i^2$, damit bekommen die Messwerte mit der kleinsten Varianz das größte Gewicht im Mittelwert. Normiert wird der gewichtete Mittelwert mit der Summe der Gewichte, sie tritt an die Stelle der Anzahl der Messwerte $n$ im arithmetischen Mittel. Die LS-Methode hat uns also "automatisch" ein Verfahren geliefert, mit dem Messwerte mit unterschiedlichen Unsicherheiten bestmöglich gemittelt werden können.


#### Lineare Regression
Der allgemeine Fall einer linearen Modellfunktion lässt sich ebenfalls analytisch lösen, dazu wird allerdings etwas lineare Algebra benötigt. Für eine lineare Regression gibt es also analytische Gleichungen, die keine numerische Minimierung erfordern und die in vielen Softwarepaketen implementiert sind. Die Modellfunktion $\boldsymbol{\lambda}=(\lambda_1,\dots,\lambda_n)^\mathsf{T}$ ist gegeben durch
$$
\boldsymbol{\lambda} = \mathbf{A}\mathbf{a}
$$
mit dem Parametervektor $\mathbf{a}=(a_1,\dots,a_m)^\mathsf{T}$, einer beliebigen von $\mathbf{a}$ unabhängigen Matrix $\mathbf{A}$ mit $m$ Zeilen und $n$ Spalten, die die Koeffizienten der $a_i$ beinhaltet, z. B. Funktionen der Positionen $x_i$ (das Beispiel Ausgleichsgerade folgt unten), und der Kovarianzmatrix $\mathbf{V}$. Zu minimieren ist also $S$ als skalare Funktion der Parameter $\mathbf{a}$
$$
S \equiv \chi^2 \overset{\textsf{lin. Regr.}}{=}
(\mathbf{y} - \mathbf{Aa})^\mathsf{T} \,
\mathbf{V}^{-1} \,
(\mathbf{y} - \mathbf{Aa}).
$$

Hier werden zunächst die Ergebnisse dieser Minimierung angegeben, die dazu notwendige Rechnung folgt für alle Interessierten im Anschluss. Der Schätzwert $\hat{\mathbf{a}}$ wird durch die Minimierung des Gradienten von $S$ bezüglich der Parameter bestimmt, er ist folgende lineare Funktion der Messwerte $\mathbf{y}$:
$$
\hat{\mathbf{a}} = 
(\mathbf{A}^\mathsf{T}\,\mathbf{V}^{-1}\,\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\,\mathbf{V}^{-1} \mathbf{y} \equiv 
\mathbf{B}\mathbf{y}.
$$
Die Kovarianzmatrix der Parameter $\hat{\mathbf{a}}$ ergibt daraus sich durch Fortpflanzung der Unsicherheiten (exakt für lineare Funktionen der Parameter):
$$
\mathbf{V}[\hat{\mathbf{a}}]= \mathbf{B}\mathbf{V}\mathbf{B}^\mathsf{T} = (\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})^{-1}
$$
(Ähnlichkeiten mit Namen von Fußballvereinen sind rein zufällig und nicht beabsichtigt).


>**Nebenrechnung 1: Schätzwert für Parametervektor $\mathbf{a}$ durch lineare Regression**
>
>Bevor der Gradient bezüglich $\mathbf{a}$ gebildet wird, multiplizieren wir zunächst $S$ aus:
>$$
S = 
\mathbf{y}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} - 
\mathbf{y}^\mathsf{T} \mathbf{V}^{-1}  \mathbf{Aa} -
(\mathbf{Aa})^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} +
(\mathbf{Aa})^\mathsf{T} \mathbf{V}^{-1} \mathbf{Aa}.
>$$
> Beachten Sie, dass jeden dieser Summanden ein Skalar ist. Für diese Nebenrechnung verwenden wir eine Matrizenschreibweise, da wir mit den bekannten Rechenregeln für Matrizen und deren Inverse und Transponierte am schnellsten und übersichtlichsten ans Ergebnis gelangen.
> Wir verwenden nun die Rechenregel für die Transponierte eines Produkts von Matrizen: $(\mathbf{AB\dots Z})^\mathsf{T} = \mathbf{Z}^\mathsf{T}\dots \mathbf{B}^\mathsf{T} \mathbf{A}^\mathsf{T}$. Damit bekommen wir im dritten und vierten Summanden $(\mathbf{Aa})^\mathsf{T}=\mathbf{a}^\mathsf{T}\mathbf{A}^\mathsf{T}$. Außerdem ziehen wir im zweiten Summanden $\mathbf{a}$ nach vorn, wobei wir beachten, dass das Inverse der Kovarianzmatrix wie die Kovarianzmatrix selbst eine symmetrische Matrix ist und somit $(\mathbf{V}^{-1})^\mathsf{T}=\mathbf{V}^{-1}$: 
>$$
(\mathbf{y}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})\mathbf{a} = 
\mathbf{a}^\mathsf{T} (\mathbf{y}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})^\mathsf{T} =
\mathbf{a}^\mathsf{T} \mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y}.
>$$
>Damit erhalten wir:
>$$
S = 
\mathbf{y}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} - 
2\mathbf{a}^\mathsf{T} \mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} +
\mathbf{a}^\mathsf{T} (\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A}) \,\mathbf{a}.
>$$
>Nun bilden wir den Gradienten von $S$ bezüglich der Parameter $\mathbf{a}$. Der erste Summand ist nicht von $\mathbf{a}$ abhängig und fällt weg, und im letzten Summanden, in dem $\mathbf{a}$ und $\mathbf{a}^\mathsf{T}$ auftreten, wird die Produktregel angewendet:
>$$
\boldsymbol\nabla_\mathbf{a} S= 
-2 \mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} 
+2 (\mathbf{A}^\mathsf{T} \mathbf{V}^{-1}  \mathbf{A}) \,\mathbf{a}.
>$$
>Der Gradient des Skalars $S$ bezüglich der Parameter ist ein Vektor. Die LS-Methode besagt, dass die notwendige Bedingung für Schätzwert für $\mathbf{a}$ das Verschwinden dieses Gradienten ist, also $\boldsymbol\nabla_\mathbf{a} S \overset{!}{=}0$ für $\mathbf{a}=\hat{\mathbf{a}}$. Wir kürzen also den Vorfaktor und lösen nach $\hat{\mathbf{a}}$ auf:
>$$
(\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})\,\hat{\mathbf{a}} = 
\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y}.
>$$
>Durch Multiplikation beider Seiten dieser Gleichung mit $(\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})^{-1}$ von links erhalten wir als Lösung
>$$
\hat{\mathbf{a}} =
(\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})^{-1}
\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} \equiv \mathbf{B} \mathbf{y},
>$$
>wobei wir das Produkt der fünf Matrizen mit $\mathbf{B}$ abgekürzt haben. Der Term in Klammern ist eine $m\times m$-Matrix, wird multipliziert mit der $m\times n$-Matrix $\mathbf{A}^\mathsf{T}$ und der $n\times n$-Matrix $\mathbf{V}^{-1}$. Damit ist $\mathbf{B}$ eine $m\times n$-Matrix.

>**Nebenrechnung 2: Schätzwert für Kovarianzmatrix des Parametervektors**  
>
>Zur Schätzung der Kovarianzmatrix $\mathbf{V}[\hat{\mathbf{a}}]$ des *Parametervektors* – nicht zu verwechseln mit der in obiger Rechnung verwendeten (inversen) Kovarianzmatrix der *Messwerte* $\mathbf{V}$ – verwenden wir das lineare Gesetz der Fortpflanzung der Unsicherheiten ("gaußsches Fehlerfortpflanzungsgesetz"), das für eine solche lineare Funktionen der Parameter exakt ist. Bisher hatten wir nur Varianzen von skalare Funktionen $u$ der Messwerte verwendet:
>$$
\mathbf{V}[u] = \sum_{kl} \frac{\partial u}{\partial x_k} \frac{\partial u}{\partial x_l} V_{kl}
>$$
>mit den Messwerten $x_i$ und den Elementen der Kovarianzmatrix der Messwerte $V_{ij}$. Wir verwenden in dieser Nebenrechnung die Komponentenschreibweise, um die Rechnung einfacher und transparenter zu machen. Die Verallgemeinerung auf Vektoren $\mathbf{u}$, die Funktionen der Messwerte sind (wie $\hat{\mathbf{a}}$), und die Elemente der Kovarianzmatrix $V_{ij}[\mathbf{u}]$ funktioniert wie folgt:
>$$
V_{ij}[\mathbf{u}] \equiv
\mathsf{Cov}(u_i,u_j) = 
\sum_{kl} \frac{\partial u_i}{\partial x_k} \frac{\partial u_j}{\partial x_l} V_{kl}.
>$$
>Angewendet auf die lineare Regression entspricht $\mathbf{u}$ dem Parametervektor $\hat{\mathbf{a}}$ und die Daten $\mathbf{x}$ den Messdaten $\mathbf{y}$. $\hat{\mathbf{a}}$ ist eine lineare Funktion der Daten: $\hat{\mathbf{a}} = \mathbf{By}$ mit obiger Definition von $\mathbf{B}$. Damit ist zu berechnen:
>$$
V_{ij}[\hat{\mathbf{a}}] =
\sum_{kl} \frac{\partial \hat{a}_i}{\partial y_k} \frac{\partial \hat{a}_j}{\partial y_l} V_{kl},
>$$
>wobei die partiellen Ableitungen lauten:
>$$
\frac{\partial \hat{a}_i}{\partial y_k} = B_{ik}, \quad
\frac{\partial \hat{a}_j}{\partial y_j} = B_{jl}.
>$$
> Damit ergibt sich
>$$
V_{ij}[\hat{\mathbf{a}}] = \sum_{kl} B_{ik} B_{jl} V_{kl} = \sum_{kl} B_{ik} V_{kl} B_{lj},
>$$ 
>wobei wir im letzten Schritt die letzten beiden Komponenten transponiert und vertauscht und dabei berücksichtigt haben, dass $\mathbf{V}$ symmetrisch ist, also $V_{lk} = V_{kl}$ gilt. Dies entspricht in Matrixschreibweise dem bereits oben angegebenen Resultat:
>$$
\mathbf{V}[\hat{\mathbf{a}}]= \mathbf{B}\mathbf{V}\mathbf{B}^\mathsf{T}.
>$$
>
>Wenn $\mathbf{B}$ schon bekannt ist, endet die Rechnung hier, ansonsten kann die Definition von $\mathbf{B}$,
>$$
\mathbf{B}\equiv
(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}.
>$$
>noch eingesetzt und vereinfacht werden, indem wie in Nebenrechnung 1 für die Transponierte eines Produkts von Matrizen $(\mathbf{AB\dots Z})^\mathsf{T} = \mathbf{Z}^\mathsf{T}\dots \mathbf{B}^\mathsf{T} \mathbf{A}^\mathsf{T}$ verwendet wird:
>$$
\begin{split}
V_{ij}[\hat{\mathbf{a}}] 
&= \left[(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\right]
\mathbf{V}
\left[(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\right]^\mathsf{T}\\
&= \left[(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\right]
\mathbf{V}
\left[(\mathbf{V}^{-1})^\mathsf{T} \mathbf{A} 
( (\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1} )^\mathsf{T}\right]\\
\end{split}
>$$
>Dieses Produkt von Matrizen kann jetzt deutlich vereinfacht werden, indem ausgenutzt wird, dass für das Produkt einer quadratischen Matrix mit ihrer Inversen gilt $\mathbf{MM}^{-1} = \mathbf{M^{-1}M} = \mathbf{1}_d$, also für eine $d\times d$-Matrix die Einheitsmatrix in $d$ Dimensionen. Dies wenden wir auf die Kovarianzmatrix und ihre Inverse in der Mitte des Produkts an. Außerdem beachten wir, dass die $n\times n$-Matrizen $\mathbf{V}$ bzw. $\mathbf{V}^{-1}$ und damit auch die $m\times m$-Matrix $\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A}$ und ihre Inverse symmetrisch sind, so dass für diese Matrizen gilt $\mathbf{M}=\mathbf{M}^\mathsf{T}$. Die Matrix $\mathbf{A}$ selbst ist nicht quadratisch und besitzt daher keine Inverse. Nun heben sich einige Matrizen und ihre Inverse heraus
>$$
\begin{split}
\mathbf{V}[\hat{\mathbf{a}}] 
&= \left[(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\right]
\mathbf{V}
\left[\mathbf{V}^{-1} \mathbf{A} 
(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}\right]\\
&= (\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}
\underbrace{\mathbf{V}\mathbf{V}^{-1}}_{\mathbf{1}_n}
\mathbf{A} 
(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}\\
&= (\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\underbrace{(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A}) 
(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}}_{\mathbf{1}_m}\\
&= (\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}.
\end{split}
>$$

#### Ausgleichsgerade

Eine Standardaufgabe der Parameterschätzung ist die Anpassung einer **linearen Modellfunktion** $\lambda_i = a_0 + a_1 x_i$ (linear in den Positionen $x_i$ und linear in den Parametern $a_0$ und $a_1$) an $n$ unkorrelierte Datenpunkte $(x_i,y_i)$ mit bekannten Varianzen $\sigma_i^2$. Dies wird im physikalischen Praktikum oft **Ausgleichsgerade** genannt. Mit der oben eingeführten Matrixschreibweise ist dann:
$$
\mathbf{a} = 
\begin{pmatrix}
a_0\\
a_1
\end{pmatrix}, \quad
\mathbf{A} = 
\begin{pmatrix}
1 & x_1\\
\vdots & \vdots\\
1 & x_n\\
\end{pmatrix},
$$
so dass sich aus dem Produkt ein Vektor von Modellfunktionen für jede Position $x_i$ ergibt:
$$
\boldsymbol{\lambda} = \mathbf{A} \,\mathbf{a} =
\begin{pmatrix}
a_0 + a_1 x_1\\
\vdots \\
a_0 + a_1 x_n\\
\end{pmatrix}.
$$
Da die Datenpunkte unkorreliert sind, ist ihre Kovarianzmatrix $\mathbf{V}$ diagonal, die Einträge auf der Diagonalen bestehen aus den Varianzen. Damit ist ihre Inverse $\mathbf{V}^{-1}$ ebenfalls diagonal und besteht aus den Kehrwerten der Varianzen. Diese bezeichnen wir (wie schon beim gewichteten Mittelwert) als Gewichte, mit der Abkürzung $w_i\equiv 1/\sigma_i^2$:
$$
\mathbf{V} =
\begin{pmatrix}
\sigma_1^2 & \cdots & 0 \\
\vdots & \ddots & \vdots \\
0 & \cdots & \sigma_n^2
\end{pmatrix} \quad\to\quad
\mathbf{V}^{-1} =
\begin{pmatrix}
\frac{1}{\sigma_1^2} & \cdots & 0 \\
\vdots & \ddots & \vdots \\
0 & \cdots & \frac{1}{\sigma_n^2}
\end{pmatrix} \equiv
\begin{pmatrix}
w_1 & \cdots & 0 \\
\vdots & \ddots & \vdots \\
0 & \cdots & w_n
\end{pmatrix}.
$$

Für diese Wahl von $\mathbf{a}$, $\mathbf{A}$ und $\mathbf{V}^{-1}$ muss jetzt der Schätzwert für die Parameter berechnet werden:
$$
\hat{\mathbf{a}} =
(\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})^{-1}
\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y}.
$$
Auch hier wird zunächst das Ergebnis angegeben, gefolgt von der Nebenrechnung weiter unten:
$$
\hat{\mathbf{a}} =
\begin{pmatrix}
\hat{a}_0\\
\hat{a}_1
\end{pmatrix} =
\frac{1}{(\sum_i w_i)(\sum_i w_i x_i^2)-(\sum_i w_i x_i)^2}
\begin{pmatrix}
(\sum w_i x_i^2)(\sum w_i y_i)  - (\sum_i w_i x_i)(\sum w_i x_i y_i) \\
(\sum_i w_i x_i)(\sum w_i x_i y_i) - (\sum w_i x_i)(\sum w_i y_i)\\
\end{pmatrix}.
$$
Wir erhalten also eine (halbwegs kompakte) Gleichung für die Schätzwerte des $y$-Achsenabschnitts $\hat{a}_0$ und die Steigung $\hat{a}_1$ der Ausgleichsgeraden. In früheren Zeiten wurde diese Gleichung im physikalischen Praktikum zum Abtippen am Taschenrechner, später am Computer, bereitgestellt. Heute ist sie in einer Reihe von Softwarewerkzeugen bereits implementiert. Ein Verständnis dafür, wie sie zustande kommt, ist dennoch für Naturwissenschaftler:innen unabdingbar.

Auch für die Kovarianzmatrix der Parameter $\hat{a}_0$ und $\hat{a}_1$ gibt es eine kompakte Darstellung:
$$
\mathbf{V}[\hat{\mathbf{a}}] =
(\mathbf{A}^\mathsf{T}\,
\mathbf{V}^{-1}\,
\mathbf{A})^{-1} =
\frac{1}{(\sum_i w_i)(\sum_i w_i x_i^2)-(\sum_i w_i x_i)^2}
\begin{pmatrix}
\sum_i w_i x_i^2 & -\sum_i w_i x_i \\
-\sum_i w_i x_i  & \sum_i w_i\\
\end{pmatrix}.
$$
Ein wesentliches Ergebnis dieser Rechnung ist, dass $y$-Achsenabschnitt und Steigung im allgemeinen **antikorreliert** sind, denn die Nicht-Diagonalelemente sind negativ und damit auch der Korrelationskoeffizient. Dies war auch zu erwarten, denn eine größere Steigung führt zu einem kleineren $y$-Achsenabschnitt und umgekehrt.

Durch eine geschickte **Koordinatentransformation** lässt sich diese Antikorrelation vermeiden. Die Idee dabei ist, die Messpunkte so zu verschieben, dass die neue $y$-Achse "in der Mitte" der Messpunkte liegt. Die Mitte ist dabei der oben besprochene gewichtete Mittelwert
$$
\overline{x} = \frac{1}{\sum_i w_i} \sum_i w_i x_i.
$$
Die Koordinatentransformation lautet:
$$
x_i \to x_i^\prime = x_i - \overline{x} = x_i - \frac{\sum_i w_i x_i}{\sum_i w_i}.
$$
Damit verschwindet das Nicht-Diagonalelement der Kovarianzmatrix:
$$
-\sum_i w_i x_i^\prime = 
-\sum_i w_i \left(  x_i - \frac{\sum_i w_i x_i}{\sum_i w_i} \right) = 
-\sum_i w_i x_i + \sum_i w_i\frac{\sum_i w_i x_i}{\sum_i w_i} = 0.
$$ 
Folgender Beispielcode zeigt dies anhand einer Ausgleichsgerade an drei Datenpunkte. Nach einer Verschiebung um den gewichteten Mittelwert verschwindet der Korrelationskoeffizient (bis auf numerische Ungenauigkeiten).


In [ ]:
"""straight-line fit without parameter correlations"""
import numpy as np
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit

n = 3
xdata  = np.array( [ 1.0, 2.0, 3.0 ] )
ydata  = np.array( [ 1.5, 3.6, 4.1 ] )
ey     = np.array( [ 0.5, 0.8, 0.3 ] )

def lin_model( x, a0=1., a1=1. ):
	'''linear model (straight-line fit)'''
	return a0 + a1*x

# plot data points
fig,ax = plt.subplots( 1,2,figsize=([15,5]) )
ax[0].errorbar( xdata, ydata, ey,fmt='bo') 
ax[0].set_xlabel('$x$')
ax[0].set_ylabel('$y$')

# fit with curve_fit (uncertainty only correct when explicitly switching on absolute uncertainites)
popt, pcov = curve_fit( lin_model, xdata, ydata, sigma=ey, absolute_sigma=True )

# plot fitted curve
xrange = np.linspace( 0.5, 3.5, 200 )
ax[0].plot( xrange, lin_model( xrange, *popt), 'r-' )

# print fit parametera
prho = pcov[1][0]/np.sqrt(pcov[0][0]*pcov[1][1])
print( "--- Before parameter transformation --- ")
print( "Parameters:                  ", popt )
print( "Correlation coefficient:     ", prho )
print( "Covariance matrix:\n", pcov )
ax[0].text( 0.5, 4.5, r"before: $\rho$ = %5.3f" % prho )

# parameter transformation
shift = np.average( xdata, weights=1./ey**2)
xdata = xdata - shift

# plot shifted data points
ax[1].errorbar( xdata, ydata, ey,fmt='bo') 
ax[1].set_xlabel( r'$x^\prime$')
ax[1].set_ylabel( r'$y$')

# fit with curve_fit (uncertainty only correct when explicitly switching on absolute uncertainites)
popt, pcov = curve_fit( lin_model, xdata, ydata, sigma=ey, absolute_sigma=True )

# plot fitted curve
xrange = np.linspace( 0.5-shift, 3.5-shift, 200 )
ax[1].plot( xrange, lin_model( xrange, *popt), 'r-' )

# print fit parameters
prho = pcov[1][0]/np.sqrt(pcov[0][0]*pcov[1][1])
print( r"--- After parameter transformation x' = x - %5.3f --- " % shift )
print( "Parameters:                  ", popt )
print( "Correlation coefficient:     ", prho )
print( "Covariance matrix:\n", pcov )
ax[1].text( 0.5-shift, 4.5, r"after: $\rho$ = %5.3e" % prho )

plt.show()

>**Nebenrechung 3: Ausgleichsgerade**
>
>In dieser Nebenrechnung sollen die Größen berechnet werden, die in die Schätzwerte für die Geradenparameter und ihre Kovarianzmatrix eingehen: 
>$$
\begin{split}
\mathbf{A}^\mathsf{T}
\mathbf{V}^{-1}
\mathbf{A} 
&= 
\begin{pmatrix}
1 & \cdots & 1 \\
x_1 & \cdots & x_n 
\end{pmatrix}
\begin{pmatrix}
w_1 & \cdots & 0 \\
\vdots & \ddots & \vdots \\
0 & \cdots & w_n
\end{pmatrix} 
\begin{pmatrix}
1 & x_1\\
\vdots & \vdots\\
1 & x_n\\
\end{pmatrix} \\
&=
\begin{pmatrix}
w_1 & \cdots & w_n \\
w_1 x_1 & \cdots & w_n x_n \\
\end{pmatrix}
\begin{pmatrix}
1 & x_1\\
\vdots & \vdots\\
1 & x_n\\
\end{pmatrix} \\
&=
\begin{pmatrix}
\sum_i w_i & \sum_i w_i x_i \\
\sum_i w_i x_i & \sum_i w_i x_i^2\\
\end{pmatrix}.
\end{split}
>$$
>Die Determinante dieser $2\times2$-Matrix ist
>$$
\mathsf{det}(\mathbf{A}^\mathsf{T} 
\mathbf{V}^{-1}
\mathbf{A}) =
\left(\sum_i w_i\right)\left(\sum_i w_i x_i^2\right)-\left(\sum_i w_i x_i\right)^2.
>$$
>Die Matrix kann leicht invertiert werden (Vertauschen der Diagonalelemente, Minuszeichen vor Nicht-Diagonalelemente, Division durch Determinante) – dieser Ausdruck wird in der Kovarianzmatrix der Parameter benötigt:
>$$
(\mathbf{A}^\mathsf{T} 
\mathbf{V}^{-1}
\mathbf{A})^{-1}
 =\frac{1}{\mathsf{det}(\mathbf{A}^\mathsf{T} \,
\mathbf{V}^{-1}\,
\mathbf{A}) }
\begin{pmatrix}
\sum_i w_i x_i^2 & -\sum_i w_i x_i \\
-\sum_i w_i x_i  & \sum_i w_i\\
\end{pmatrix}.
>$$
>Für den Schätzwert der Parameter wird noch benötigt:
>$$
\mathbf{A}^\mathsf{T}
\mathbf{V}^{-1}
\mathbf{y} = 
\begin{pmatrix}
w_1 & \cdots & w_n \\
w_1 x_1 & \cdots & w_n x_n \\
\end{pmatrix}
\begin{pmatrix}
y_1\\
\vdots\\
y_n
\end{pmatrix} =
\begin{pmatrix}
\sum_i w_i y_i \\
\sum_i w_i x_i y_i
\end{pmatrix}
>$$
> und damit schließlich:
>$$
\begin{split}
\hat{\mathbf{a}} &=
\begin{pmatrix}
\hat{a}_0\\
\hat{a}_1
\end{pmatrix} =
(\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})^{-1}
\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} \\
&=\frac{1}{\mathsf{det}(\mathbf{A}^\mathsf{T} \,
\mathbf{V}^{-1}\,
\mathbf{A}) }
\begin{pmatrix}
\sum_i w_i x_i^2 & -\sum_i w_i x_i \\
-\sum_i w_i x_i  & \sum_i w_i\\
\end{pmatrix} 
\begin{pmatrix}
\sum_i w_i y_i \\
\sum_i w_i x_i y_i
\end{pmatrix} \\
&=\frac{1}{(\sum_i w_i)(\sum_i w_i x_i^2)-(\sum_i w_i x_i)^2}
\begin{pmatrix}
(\sum w_i x_i^2)(\sum w_i y_i)  - (\sum_i w_i x_i)(\sum w_i x_i y_i) \\
(\sum_i w_i x_i)(\sum w_i x_i y_i) - (\sum w_i x_i)(\sum w_i y_i)\\
\end{pmatrix}.
\end{split}
>$$

### Güte der Anpassung
In der Methode der kleinsten Quadrate (LS-Methode) wird eine vorgegebene Modellfunktion $\boldsymbol{\lambda}$ mit Daten verglichen und die Parameter der Funktion so angepasst, dass sie am besten zu den Daten passen. Dabei bedeutet "am besten" im Sinne der LS-Methode, dass die Summe der Residuenquadrate,
$$
S \equiv \chi^2 \equiv
(\mathbf{y} - \boldsymbol{\lambda}(\mathbf{x};\mathbf{a}))^\mathsf{T} \,
\mathbf{V}^{-1} \,
(\mathbf{y} - \boldsymbol{\lambda}(\mathbf{x};\mathbf{a})),
$$
minimiert wird. Das bedeutet allerdings noch nicht, dass die Modellfunktion sinnvoll gewählt war und die Daten gut beschreibt. So führt eine Anpassung einer linearen Funktion an Daten, die nicht mit einer Geraden kompatibel sind, zu einem "schlechten" Fit. Außerdem resultiert ein "schlechter" Fit, wenn die Kovarianzmatrix $\mathbf{V}$ der Modellfunktion zu große oder zu kleine Unsicherheiten oder falsche Korrelationen annimmt.

Gesucht ist ein Kriterium, um die **Güte der Anpassung** (engl.: goodness of fit, GoF) zu quantifizieren. Für die LS-Methode gibt es ein solches Kriterium, weil die Wahrscheinlichkeitsverteilung von $S$ bekannt ist: zumindest für normalverteilte Messwerte folgt $S$ einer $\chi^2$-Verteilung.  Wird nun nach Minimierung von $S$ ein Wert von $S$ gefunden, der anhand der $\chi^2$-Verteilung sehr unwahrscheinlich ist, dann ist das ein Anzeichen dafür, dass entweder die **Modellfunktion ungeeignet** ist oder die **Unsicherheiten falsch abgeschätzt** wurden. 

Für $n$ normalverteile Messwerte $y_i$ und $m$ Modellparameter $a_j$ folgt die Summe der Residuenquadrate einer $\chi^2$-Verteilung (vgl. Kapitel 2) mit $n_\mathsf{dof}=n-m$ Freiheitsgraden (engl.: degrees of freedom, dof):
$$
\chi^2(S;n_\mathsf{dof}) = \frac{S^{\frac{n_\mathsf{dof}}{2}-1}}
{2^{\frac{n_\mathsf{dof}}{2}}\Gamma(\frac{n_\mathsf{dof}}{2})}
\exp\left[-\frac{S}{2}\right].
$$
Wenn aus $n$ Datenpunkten $m$ Parameter zu bestimmen sind, dann ist die Zahl der Freiheitsgrade also gerade die Differenz $n-m$, damit ist $n_\mathsf{dof}$ ein Maß dafür, wie viel Überschuss an Datenpunkten im Vergleich zu den zu bestimmenden Parametern vorhanden ist, wieviele Datenpunkte also im Mittel "noch frei" und nicht zur Festlegung der Parameter notwendig sind. Zur Erinnerung: der Erwartungswert der $\chi^2$-PDF ist $\mathsf{E}[S]=n_\mathsf{dof}$ und die Varianz $\mathsf{V}[S]=2n_\mathsf{dof}$.

Mit dieser bekannten Wahrscheinlichkeitsverteilung kann deren integrierte Wahrscheinlichkeit für einen Test der Güte der Anpassung (engl.: goodness-of-fit test) herangezogen werden. Das Maß für Güte der Anpassung ist die **$\chi^2$-Wahrscheinlichkeit** $P_{\chi^2}$. Diese ist definiert als die Wahrscheinlichkeit, einen **beobachteten Wert von $S_0$ oder größer zu finden**:
$$
P_{\chi^2} = \int_{S_0}^\infty \chi^2(S;n_\mathsf{dof}) \,\mathsf{d} S.
$$
Dies entspricht gerade der Gesamtwahrscheinlichkeit 1 minus der CDF der $\chi^2$-Verteilung für den Wert $S_0$. In SciPy kann dieser Wert über `1.–scipy.stats.chi2.cdf(S0,ndof)` berechnet werden. Auch wenn die $\chi^2$-CDF gerade nicht verfügbar ist, kann die Güte der Anpassung näherungsweise überprüft werden, in dem die Wahrscheinlichkeit für $S_0$ auf die Zahl der Freiheitsgrade  $n_\mathsf{dof}$ normiert wird. Wie in unten stehender Abbildung gezeigt wird, beträgt die Wahrscheinlichkeit für $S_0/n_\mathsf{dof}$ ungefähr 40%, näherungsweise unabhängig von $n_\mathsf{dof}$. Daher kann diese Größe $S_0/n_\mathsf{dof}$ als **näherungsweises Maß für die Güte der Anpassung** verwendet werden: eine gute Anpassung besitzt $S_0/n_\mathsf{dof}\approx 1$. Falls $S_0/n_\mathsf{dof}$ viel größer oder viel kleiner ist als 1, ist entweder die Modellfunktion ungeeignet oder die Unsicherheiten wurden falsch abgeschätzt.

In [ ]:
""" display chi2 probability and chi2 probability normalized to number of degrees of freedom"""
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import chi2

fig,ax = plt.subplots( 1, 2, figsize=(10,5) )

S = np.linspace( 0, 25, 250 )
ndof = np.array( [ 2, 4, 6, 8, 10 ] )
for n in ndof:
    ax[0].plot( S, 1.-chi2.cdf( S, n ), label=r'$n_\mathsf{dof}$ = %d' % n  )
    ax[1].plot( S/n, (1.-chi2.cdf( S, n ) ) )

ax[0].set_xlabel( r'$\chi^2$' )
ax[0].set_ylabel( r'$P_{\chi^2}$' )
ax[0].set_ylim( 0., 1.05 )
ax[0].legend()

ax[1].vlines( 1, 0, 1, linestyles="dashed", colors="red" )
ax[1].set_xlabel( r'$\chi^2/n_\mathsf{dof}$' )
ax[1].set_ylabel( r'$P_{\chi^2}$' )
ax[1].set_xlim( 0, 3 )
ax[1].set_ylim( 0., 1.05 )

plt.show()